In [ ]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from PIL import Image
import numpy as np
import pandas as pd
from datetime import datetime


In [41]:


def load_trained_model(model_path):
    """Load the trained model from checkpoint"""
    # Initialize the same model architecture
    base_model = models.resnet18(weights='IMAGENET1K_V1')
    num_features = base_model.fc.in_features
    base_model.fc = nn.Sequential(
        nn.Linear(num_features, 256),
        nn.ReLU(),
        nn.Dropout(0.2),
        nn.Linear(256, 13),
        nn.Sigmoid()
    )
    
    # Get device
    device = torch.device("mps") if torch.backends.mps.is_available() else torch.device("cpu")
    
    # Load checkpoint
    checkpoint = torch.load(model_path, map_location=device)
    base_model.load_state_dict(checkpoint['model_state_dict'])
    base_model = base_model.to(device)
    
    return base_model, device

def load_and_transform_image(image_path):
    """Load and transform a single image from path"""
    transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], 
                           std=[0.229, 0.224, 0.225])
    ])
    
    try:
        img = Image.open(image_path).convert('RGB')
        return transform(img)
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        return None

def predict(image_path, model, device):
    """Make prediction for a single image"""
    img_tensor = load_and_transform_image(image_path)
    if img_tensor is None:
        return None
    
    model.eval()
    with torch.no_grad():
        outputs = model(img_tensor.unsqueeze(0).to(device))
        
    return outputs.cpu().numpy()

def classify_images(image_paths, model_path='best_model.pth', confidence_threshold=0.5):
    """Classify multiple images using the trained model"""
    # Categories in the same order as training
    categories = ['fruit', 'bread', 'cookware', 'seafood', 'wine', 
                 'meal', 'cheese', 'meat', 'food', 'beverage', 
                 'dairy', 'vegetable', 'dessert']
    
    # Load model
    model, device = load_trained_model(model_path)
    model.eval()
    
    results = []
    for image_path in image_paths:
        try:
            # Get prediction
            pred = predict(image_path, model, device)
            
            if pred is None:
                raise Exception("Failed to process image")
                
            pred = pred[0]  # Get first (and only) prediction
            
            # Get categories where prediction exceeds threshold
            detected_categories = [
                (cat, float(score)) 
                for cat, score in zip(categories, pred) 
                if score > confidence_threshold
            ]
            
            # Sort by confidence
            detected_categories.sort(key=lambda x: x[1], reverse=True)
            
            results.append({
                'image_path': image_path,
                'predictions': detected_categories
            })
            
        except Exception as e:
            print(f"Error processing {image_path}: {e}")
            results.append({
                'image_path': image_path,
                'error': str(e)
            })
    
    return results


In [42]:
data = pd.read_csv('data/paintings_image_path.csv')
#images_to_cat = data.sample(10)
images_to_cat = data.copy()
images_paths = images_to_cat['image_path'].tolist()
data

image_path  \
0      img/img_512/Intérieur de cuisine - Joachim Beu...   
1      img/img_512/Pieter Bruegel the Elder- The Harv...   
2                img/img_512/The Luncheon (SM sg170).png   
3      img/img_512/Paul de Vos and Jacob Jordaens - C...   
4      img/img_512/OA Hermansen, Et frokostbord, 1884...   
...                                                  ...   
64970     img/img_512/Ivan Žabota - mrs. Ležovičovej.jpg   
64971  img/img_512/Alex Colville - Infantry, near Nij...   
64972       img/img_512/Ivan Žabota - Marta Krásovej.jpg   
64973       img/img_512/Ivan Žabota - ženski portret.jpg   
64974  img/img_512/Ľudovít Pitthordt - Vlastná podobi...   

                                           item  
0      http://www.wikidata.org/entity/Q27064304  
1        http://www.wikidata.org/entity/Q776175  
2      http://www.wikidata.org/entity/Q12900365  
3      http://www.wikidata.org/entity/Q27974915  
4      http://www.wikidata.org/entity/Q20532659  
...                                         ...  
64970  http://www.wikidata.org/entity/Q51243217  
64971  http://www.wikidata.org/entity/Q51247485  
64972  http://www.wikidata.org/entity/Q51235353  
64973  http://www.wikidata.org/entity/Q51265369  
64974  http://www.wikidata.org/entity/Q51246257  

[64975 rows x 2 columns]

In [ ]:


# Example usage
if __name__ == "__main__":
    # List of images to classify
    test_images = [
        "path/to/image1.jpg",
        "path/to/image2.jpg",
    ]
    
    # Classify images
    results = classify_images(images_paths, model_path='best_model.pth', confidence_threshold=0.5)
    results_df = pd.DataFrame(results)
    display(results_df)
    
    final_df = pd.merge(images_to_cat, results_df, on='image_path')
    display(final_df)
    
    # Add timestamp
    timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    final_df['timestamp'] = timestamp

    # Save to CSV
    final_df.to_csv('data/paintings_with_food_cv.csv', index=False)
    # Print results
    for result in results:
        print(f"\nImage: {result['image_path']}")
        if 'error' in result:
            print(f"Error: {result['error']}")
        else:
            print("Detected categories:")
            for category, confidence in result['predictions']:
                print(f"- {category}: {confidence:.2%}")

/var/folders/7w/s5bmwwgs2176bk3y33c2nv2m0000gn/T/ipykernel_19827/4090545893.py:18: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(model_path, map_loca

image_path predictions
0      img/img_512/Intérieur de cuisine - Joachim Beu...          []
1      img/img_512/Pieter Bruegel the Elder- The Harv...          []
2                img/img_512/The Luncheon (SM sg170).png          []
3      img/img_512/Paul de Vos and Jacob Jordaens - C...          []
4      img/img_512/OA Hermansen, Et frokostbord, 1884...          []
...                                                  ...         ...
64970     img/img_512/Ivan Žabota - mrs. Ležovičovej.jpg          []
64971  img/img_512/Alex Colville - Infantry, near Nij...          []
64972       img/img_512/Ivan Žabota - Marta Krásovej.jpg          []
64973       img/img_512/Ivan Žabota - ženski portret.jpg          []
64974  img/img_512/Ľudovít Pitthordt - Vlastná podobi...          []

[64975 rows x 2 columns]

image_path  \
0      img/img_512/Intérieur de cuisine - Joachim Beu...   
1      img/img_512/Pieter Bruegel the Elder- The Harv...   
2                img/img_512/The Luncheon (SM sg170).png   
3      img/img_512/Paul de Vos and Jacob Jordaens - C...   
4      img/img_512/OA Hermansen, Et frokostbord, 1884...   
...                                                  ...   
65084     img/img_512/Ivan Žabota - mrs. Ležovičovej.jpg   
65085  img/img_512/Alex Colville - Infantry, near Nij...   
65086       img/img_512/Ivan Žabota - Marta Krásovej.jpg   
65087       img/img_512/Ivan Žabota - ženski portret.jpg   
65088  img/img_512/Ľudovít Pitthordt - Vlastná podobi...   

                                           item predictions  
0      http://www.wikidata.org/entity/Q27064304          []  
1        http://www.wikidata.org/entity/Q776175          []  
2      http://www.wikidata.org/entity/Q12900365          []  
3      http://www.wikidata.org/entity/Q27974915          []  
4      http://www.wikidata.org/entity/Q20532659          []  
...                                         ...         ...  
65084  http://www.wikidata.org/entity/Q51243217          []  
65085  http://www.wikidata.org/entity/Q51247485          []  
65086  http://www.wikidata.org/entity/Q51235353          []  
65087  http://www.wikidata.org/entity/Q51265369          []  
65088  http://www.wikidata.org/entity/Q51246257          []  

[65089 rows x 3 columns]


Image: img/img_512/Intérieur de cuisine - Joachim Beuckelaer - Musée du louvre Peintures RF 2659.jpg
Detected categories:

Image: img/img_512/Pieter Bruegel the Elder- The Harvesters - Google Art Project.jpg
Detected categories:

Image: img/img_512/The Luncheon (SM sg170).png
Detected categories:

Image: img/img_512/Paul de Vos and Jacob Jordaens - Cook at the Table with Game.jpg
Detected categories:

Image: img/img_512/OA Hermansen, Et frokostbord, 1884, KMS3132, Statens Museum for Kunst.jpg
Detected categories:

Image: img/img_512/Pieter Claesz. - Stilleven.jpg
Detected categories:

Image: img/img_512/Willem Clasz. Heda - Breakfast Table with Blackberry Pie - Google Art Project.jpg
Detected categories:

Image: img/img_512/Laurits Andersen Ring - Ved frokostbordet og morgenaviserne.jpg
Detected categories:

Image: img/img_512/Claude Monet - Le dejeurner sur l'herbe (left panel).jpg
Detected categories:

Image: img/img_512/Pieter Claesz - Breakfast Piece - Walters 371984.jpg
Detected 